# "Density" statistics & density plot

Statistics "density" are calculated on the sample of a single continuous variable.
It approximates the Probability Density Function (PDF) of this sample.
"Density" statistic samples this function point.
It's weighted, it means the counted density depends on observation weights.

This notebook uses definitions from [DataFrame](https://kotlin.github.io/dataframe/overview.html).

## Usage

"Density" statistic is useful when you have a large dataset,
and you want to understand the underlying probability distribution.
Density plot visualizes the PDF and also allows you to compare the distribution of different samples.
This is a useful alternative to the histogram for continuous data that comes from an underlying smooth distribution.

## Arguments

* Input (mandatory):
    - `x` — numeric sample on which the statistics are calculated
* Weights (optional):
    - `weights` — set of weights of the same size as the input sample.
      `null` (by default) means all weights are equal to `1.0` and the weighted density is equal to the normal one
* Parameters (optional):
    - `n: Int` — number of sampled points;
    - `trim: Boolean` — if `false`, each density is computed on the full range of the data,
      if `true`, each density is computed over the range of that group (only for grouped inputs).
    - `adjust: Double` — adjusts the value of bandwidth by multiplying it; changes how smooth the frequency curve is.
    - `kernel: Kernel` — the kernel used to calculate the density function:
        - `Kernel.GAUSSIAN`
        - `Kernel.RECTANGULAR`
        - `Kernel.TRIANGULAR`
        - `Kernel.BIWEIGHT`
        - `Kernel.EPANECHNIKOV`
        - `Kernel.OPTCOSINE`
    - `fullScanMax: Int` — maximum size of data to use density computation with 'full scan'.
      For bigger data, less accurate but more efficient density computation is applied
    - `bandWidth: BandWidth` — the method (or exact value) of bandwidth:
        - `BandWidth.Method.NRD`
        - `BandWidth.Method.NRD0`
        - `BandWidth.value(value: Double)`

### Generalized signature

The specific signature depends on the function,
but all functions related to "density"
statistic (which will be discussed further below — different variations of `statDensity()`, `densityPlot()`)
have approximately the same signature with the arguments above:

```
statDensityArgs := 
   x, 
   weights = null,
   n: Int = 512,
   trim: Boolean = false,
   adjust: Double = 1.0,
   kernel: Kernel = Kernel.GAUSSIAN,
   fullScanMax: Int = 5000,
   bandWidth: BandWidth = BandWidth.Method.NRD0,
```

The possible types of `x` and `weights` depend on where a certain function is used.
They can be simply `Iterable` (`List`, `Set`, etc.) or a reference to a column in a `DataFrame`
(`String`, `ColumnAccessor`) or the `DataColumn` itself.

## Output statistics

| name                 | type   | description                                 |
|----------------------|--------|---------------------------------------------|
| Stat.x               | Double | `x` coordinate                              |
| Stat.density         | Double | Density estimate                            |
| Stat.densityWeighted | Double | Weighted density                            |
| Stat.scaled          | Double | Density estimate, scaled to maximin of 1.0. |
| Stat.scaledWeighted  | Double | Weighted scaled                             |

## StatDensity plots

In [1]:
%useLatestDescriptors
%use kandy
%use dataframe

import org.apache.commons.math3.distribution.NormalDistribution
import org.apache.commons.math3.distribution.UniformRealDistribution
import org.jetbrains.kotlinx.statistics.dataframe.stat.mean

In [2]:
// To generate the data, we use a standard java math library
// https://commons.apache.org/proper/commons-math/
// Generate sample from normal distribution
val depthList = NormalDistribution(500.0, 100.0).sample(1000).toList()
// Generate sample from uniform distribution
val coeffList = UniformRealDistribution(0.0, 1.0).sample(1000).toList()

In [3]:
// Gather them into the DataFrame
val df = dataFrameOf(
    "depth" to depthList,
    "coeff" to coeffList
)
df.head()

<iframe onload="o_resize_iframe_out_1()" style="width:100%;" class="result_container" id="iframe_out_1" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_838860800"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let

`df` has a signature

| depth | coeff |
|-------|-------|

Let's take a look at `StatDensity` output DataFrame:

In [4]:
df.statDensity("depth", "coeff").head(5)

<iframe onload="o_resize_iframe_out_2()" style="width:100%;" class="result_container" id="iframe_out_2" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_838860802"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 1</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let

It has the following signature:

<table>
  <thead>
    <tr>
      <th alignt="left" colspan="5">Stat</th>
    </tr>
  </thead>
  <thead>
    <tr>
      <th>x</th>
      <th>density</th>
      <th>densityWeighted</th>
      <th>scaled</th>
      <th>scaledWeighted</th>
    </tr>
  </thead>
</table>

As you can see, we got a `DataFrame` with one `ColumnGroup` called `Stat` which contains several columns with statics.
For `statDensity`, each row corresponds to one PDF point.
`Stat.x` is the column with this point `x` coordinate.
`Stat.density` contains the estimated density.
`Stat.densityWeighted` — weighted version of `density`.
`Stat.scaled` is a density scaled to a maximum of 1.0.
`Stat.scaledWeighted` — weighted version of `scaled`.
`DataFrame` with "density" statistics is called `StatDensityFrame`

### `statDensity` transform

`statDensity(statDensityArgs) { /*new plotting context*/ }` modifies a plotting context —
instead of original data (no matter was it empty or not) new `StatDensity` dataset
(calculated on given arguments, inputs and weights can be provided as `Iterable` or as dataset column reference —
by name as a `String`, as a `ColumnReference` or as a `DataColumn`) is used inside a new context
(original dataset and primary context are not affected —
you can add layers using initial dataset outside the `statDensity` context).
Since the old dataset is irrelevant, we cannot use references for its columns.
But we can refer to the new ones.
They are all contained in the `Stat` group and can be called inside the new context:

In [5]:
plot {
    statDensity(depthList, adjust = 0.2) {
        // New `StatDensity` dataset here
        line {
            // Use `Stat.*` columns for mappings
            x(Stat.x)
            y(Stat.density)
            color(Stat.density)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="AIrLzZ"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"scale_mapper_kind":"color_gradient",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"density"
},
"stat":"identity",
"data":{
"density":[8.676609331544283E-5,8.327998564081704E-5,7.36397720954079E-5,5.9988144091533493E-5,4.501939063763521E-5,3.112540382180409E-5,1.982492592079031E-5,1.1632936240511975E-5,6.288518145680773E-6,3.1317600889725165E-6,1.436844758429157E-6,6.073127613351072E-7,2.3648095032535816E-7,8.483227484129286E-8,2.803543249905545E-8,8.535610786988698E-9,2.3941047224948857E-9,6.18632726818157E-10,1.4726660378567562E-10,3.229776932698642E-11,6.5340950459885595E-12,1.2745109506026473E-12,5.781740497048504E-13,2.134194882232706E-12,1.1001252038968916E-11,5.301611937071591E-11,2.3547123465152327E-10,9.635199157052533E-10,3.6322489840717016E-9,1.2615046324299459E-8,4.036552159475427E-8,1.1900273751488838E-7,3.2326133970581883E-7,8.091742018398977E-7,1.8667533514949583E-6,3.970014119469637E-6,7.786126249598312E-6,1.4090753771715816E-5,2.355252252930848E-5,3.641371985613978E-5,5.2190525800168135E-5,6.958007678952084E-5,8.671325945176447E-5,1.0171110494903896E-4,1.1328654018307402E-4,1.2105584197729673E-4,1.2539077710552204E-4,1.2696143354757995E-4,1.2633890754081014E-4,1.2394428112086144E-4,1.2029682425448872E-4,1.1621785777622585E-4,1.1266274281887705E-4,1.10187806930934E-4,1.0842925218897398E-4,1.0605142977523456E-4,1.0132792094624995E-4,9.307712652728122E-5,8.142375329420124E-5,6.796994754741194E-5,5.5318543717379234E-5,4.621921537764544E-5,4.270881520154652E-5,4.550691935042574E-5,5.37683715111557E-5,6.521310711750616E-5,7.663362355797789E-5,8.47204971075346E-5,8.700443407962986E-5,8.258081051401881E-5,7.230474578054384E-5,5.836763550477826E-5,4.346858427268532E-5,2.997848890542851E-5,1.9448971675279955E-5,1.2598160606432727E-5,9.667463526694345E-6,1.0914759858934726E-5,1.701116451927033E-5,2.918347195820569E-5,4.903175869092144E-5,7.803303993329168E-5,1.1683155969809587E-4,1.6452178324897175E-4,2.182206945258472E-4,2.7322916033265253E-4,3.239197960999049E-4,3.6515431189779673E-4,3.936682132871652E-4,4.087323208092382E-4,4.117158551050971E-4,4.048379760931567E-4,3.8996098416695286E-4,3.6826739354606496E-4,3.4099979174427445E-4,3.106031639736427E-4,2.812583082737641E-4,2.582132268833652E-4,2.4616527828596584E-4,2.47569296726275E-4,2.6173813346650707E-4,2.850802561406536E-4,3.122363804009796E-4,3.376000572484266E-4,3.567654739571538E-4,3.676204611108079E-4,3.7089714777021097E-4,3.700101442326151E-4,3.7010211033961215E-4,3.7647649111188244E-4,3.929287583563767E-4,4.206436663877731E-4,4.5811636413750986E-4,5.020374750208689E-4,5.485662847415787E-4,5.942535567629775E-4,6.361926250073792E-4,6.715663593440074E-4,6.972140234716374E-4,7.098459364756224E-4,7.07070710847624E-4,6.88774114777253E-4,6.580231257340322E-4,6.20820794153719E-4,5.84623116077639E-4,5.561842532795609E-4,5.396340070613918E-4,5.355557290021492E-4,5.413603698921462E-4,5.527232625148039E-4,5.654893642318798E-4,5.773432105916026E-4,5.88664178722132E-4,6.022907315656287E-4,6.223147608991307E-4,6.523889708250565E-4,6.942087839668744E-4,7.467366298109905E-4,8.06402209765268E-4,8.68086124499618E-4,9.263800107177589E-4,9.76581382519426E-4,0.0010151578693349758,0.0010398396995635704,0.001049766209923587,0.001045978029217642,0.0010320616175703908,0.0010143002951887984,0.0010007103099975078,9.989452135051923E-4,0.0010138427542294472,0.0010457678535748674,0.0010905783449095998,0.001141249956046447,0.

### DensityPlot layer

Density plot is a statistical plot used for visualizing the distribution of continuous variables.
It's an area graph of kernel-estimated PDF.
So basically, we can build a histogram with `statDensity` as follows:

In [6]:
val statDensityAndAreaPlot = df.plot {
    statDensity("depth") {
        area {
            x(Stat.x)
            y(Stat.density)
        }
    }
    layout.title = "`statDensity()` + `area()` layer"
}
statDensityAndAreaPlot

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="HJnJlt"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[1.8538371071279594E-5,1.8702837430147296E-5,1.8837187683082854E-5,1.8945031302750088E-5,1.9030671100107746E-5,1.909906778065367E-5,1.9155792330540664E-5,1.920696670762824E-5,1.9259193541397925E-5,1.9319475763561464E-5,1.9395127294073153E-5,1.9493676091555456E-5,1.9622761039838407E-5,1.97900242809183E-5,2.0003000717241172E-5,2.0269006491394745E-5,2.059502830811369E-5,2.0987615491441248E-5,2.1452776668774027E-5,2.1995882943466233E-5,2.2621579359044262E-5,2.333370637143297E-5,2.413523293164272E-5,2.5028202640983903E-5,2.601369427509836E-5,2.709179778314753E-5,2.8261606655815497E-5,2.9521227322089023E-5,3.086780598211125E-5,3.229757301419527E-5,3.38059048111979E-5,3.538740260823528E-5,3.703598756401141E-5,3.8745011056194056E-5,4.05073788521382E-5,4.231568752512684E-5,4.416237120881484E-5,4.603985652465865E-5,4.7940723284858945E-5,4.985786837280905E-5,5.178467004013704E-5,5.3715149739731556E-5,5.564412854270669E-5,5.756737516846214E-5,5.948174269433965E-5,6.138529110734412E-5,6.327739301632628E-5,6.515882005895456E-5,6.703180781242547E-5,6.890009734744764E-5,7.076895194738353E-5,7.264514794293517E-5,7.45369390803979E-5,7.645399433994152E-5,7.840730964011254E-5,8.040909439521134E-5,8.247263442199563E-5,8.461213320927949E-5,8.68425340560435E-5,8.917932603820455E-5,9.163833716897603E-5,9.423551846113554E-5,9.698672287076071E-5,9.99074832916003E-5,1.0301279386934995E-4,1.0631689890973967E-4,1.0983309355980657E-4,1.1357354024681136E-4,1.1754910456540577E-4,1.2176921391523796E-4,1.2624174171533322E-4,1.3097291946840376E-4,1.3596727833044644E-4,1.412276211738398E-4,1.4675502543294138E-4,1.5254887630896638E-4,1.586069292057528E-4,1.6492539959053892E-4,1.7149907784443303E-4,1.7832146610539295E-4,1.8538493362998024E-4,1.926808868244742E-4,2.0019994983344714E-4,2.0793215143355434E-4,2.158671139668049E-4,2.2399424016141336E-4,2.323028939254076E-4,2.4078257154987098E-4,2.4942306021225497E-4,2.5821458120881447E-4,2.6714791594891336E-4,2.7621451339015666E-4,2.8540657825765686E-4,2.9471714004828124E-4,3.0414010344661586E-4,3.1367028135015986E-4,3.233034121957169E-4,3.3303616367905023E-4,3.428661252516154E-4,3.527917919520535E-4,3.6281254218178537E-4,3.7292861196417976E-4,3.831410680414861E-4,3.9345178187387875E-4,4.0386340622590086E-4,4.143793555766351E-4,4.2500379109290204E-4,4.357416103837511E-4,4.465984417342284E-4,4.5758064202121014E-4,4.686952970670941E-4,4.799502228088617E-4,4.913539653675687E-4,5.029157979098003E-4,5.146457121064296E-4,5.265544020182202E-4,5.386532383710128E-4,5.509542314183592E-4,5.634699809154388E-4,5.762136121295685E-4,5.891986972713022E-4,6.02439162225268E-4,6.159491789697411E-4,6.297430445765536E-4,6.438350481571306E-4,6.582393275470657E-4,6.729697178843828E-4,6.88039594522338E-4,7.034617129174748E-4,7.192480482430112E-4,7.354096374960347E-4,7.519564267986039E-4,7.688971264453472E-4,7.862390760345199E-4,8.039881217497751E-4,8.221485075511734E-4,8.40722781702813E-4,8.597117197271383E-4,8.791142645477757E-4,8.989274842773233E-4,9.191465478352465E-4,9.397647183518781E-4,9.607733641330103E-4,9.821619868268816E-4,0.001003918266350207,0.0010260281220874164,0.0010484757898701314,0.0010712439142628665,0.0010943136557152698,0.0011176648121798915,0.0011412759548260242,0.0011651245774952784,0.0011891872595340648,0.0012134398415962417,0.0012378576139319348,0.0012624155165650154

But we can do it even faster with `densityPlot(statDensityArgs)` method:

In [7]:
val densityLayerPlot = plot {
    densityPlot(depthList)
    layout.title = "`densityPlot()` layer"
}
densityLayerPlot

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="k2UJaX"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"`densityPlot()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[1.8538371071279594E-5,1.8702837430147296E-5,1.8837187683082854E-5,1.8945031302750088E-5,1.9030671100107746E-5,1.909906778065367E-5,1.9155792330540664E-5,1.920696670762824E-5,1.9259193541397925E-5,1.9319475763561464E-5,1.9395127294073153E-5,1.9493676091555456E-5,1.9622761039838407E-5,1.97900242809183E-5,2.0003000717241172E-5,2.0269006491394745E-5,2.059502830811369E-5,2.0987615491441248E-5,2.1452776668774027E-5,2.1995882943466233E-5,2.2621579359044262E-5,2.333370637143297E-5,2.413523293164272E-5,2.5028202640983903E-5,2.601369427509836E-5,2.709179778314753E-5,2.8261606655815497E-5,2.9521227322089023E-5,3.086780598211125E-5,3.229757301419527E-5,3.38059048111979E-5,3.538740260823528E-5,3.703598756401141E-5,3.8745011056194056E-5,4.05073788521382E-5,4.231568752512684E-5,4.416237120881484E-5,4.603985652465865E-5,4.7940723284858945E-5,4.985786837280905E-5,5.178467004013704E-5,5.3715149739731556E-5,5.564412854270669E-5,5.756737516846214E-5,5.948174269433965E-5,6.138529110734412E-5,6.327739301632628E-5,6.515882005895456E-5,6.703180781242547E-5,6.890009734744764E-5,7.076895194738353E-5,7.264514794293517E-5,7.45369390803979E-5,7.645399433994152E-5,7.840730964011254E-5,8.040909439521134E-5,8.247263442199563E-5,8.461213320927949E-5,8.68425340560435E-5,8.917932603820455E-5,9.163833716897603E-5,9.423551846113554E-5,9.698672287076071E-5,9.99074832916003E-5,1.0301279386934995E-4,1.0631689890973967E-4,1.0983309355980657E-4,1.1357354024681136E-4,1.1754910456540577E-4,1.2176921391523796E-4,1.2624174171533322E-4,1.3097291946840376E-4,1.3596727833044644E-4,1.412276211738398E-4,1.4675502543294138E-4,1.5254887630896638E-4,1.586069292057528E-4,1.6492539959053892E-4,1.7149907784443303E-4,1.7832146610539295E-4,1.8538493362998024E-4,1.926808868244742E-4,2.0019994983344714E-4,2.0793215143355434E-4,2.158671139668049E-4,2.2399424016141336E-4,2.323028939254076E-4,2.4078257154987098E-4,2.4942306021225497E-4,2.5821458120881447E-4,2.6714791594891336E-4,2.7621451339015666E-4,2.8540657825765686E-4,2.9471714004828124E-4,3.0414010344661586E-4,3.1367028135015986E-4,3.233034121957169E-4,3.3303616367905023E-4,3.428661252516154E-4,3.527917919520535E-4,3.6281254218178537E-4,3.7292861196417976E-4,3.831410680414861E-4,3.9345178187387875E-4,4.0386340622590086E-4,4.143793555766351E-4,4.2500379109290204E-4,4.357416103837511E-4,4.465984417342284E-4,4.5758064202121014E-4,4.686952970670941E-4,4.799502228088617E-4,4.913539653675687E-4,5.029157979098003E-4,5.146457121064296E-4,5.265544020182202E-4,5.386532383710128E-4,5.509542314183592E-4,5.634699809154388E-4,5.762136121295685E-4,5.891986972713022E-4,6.02439162225268E-4,6.159491789697411E-4,6.297430445765536E-4,6.438350481571306E-4,6.582393275470657E-4,6.729697178843828E-4,6.88039594522338E-4,7.034617129174748E-4,7.192480482430112E-4,7.354096374960347E-4,7.519564267986039E-4,7.688971264453472E-4,7.862390760345199E-4,8.039881217497751E-4,8.221485075511734E-4,8.40722781702813E-4,8.597117197271383E-4,8.791142645477757E-4,8.989274842773233E-4,9.191465478352465E-4,9.397647183518781E-4,9.607733641330103E-4,9.821619868268816E-4,0.001003918266350207,0.0010260281220874164,0.0010484757898701314,0.0010712439142628665,0.0010943136557152698,0.0011176648121798915,0.0011412759548260242,0.0011651245774952784,0.0011891872595340648,0.0012134398415962417,

Let's compare them:

In [8]:
plotGrid(listOf(statDensityAndAreaPlot, densityLayerPlot))

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="iE6Vmm"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"layout":{
"name":"grid",
"ncol":2,
"nrow":1,
"fit":true,
"align":false
},
"figures":[{
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[1.8538371071279594E-5,1.8702837430147296E-5,1.8837187683082854E-5,1.8945031302750088E-5,1.9030671100107746E-5,1.909906778065367E-5,1.9155792330540664E-5,1.920696670762824E-5,1.9259193541397925E-5,1.9319475763561464E-5,1.9395127294073153E-5,1.9493676091555456E-5,1.9622761039838407E-5,1.97900242809183E-5,2.0003000717241172E-5,2.0269006491394745E-5,2.059502830811369E-5,2.0987615491441248E-5,2.1452776668774027E-5,2.1995882943466233E-5,2.2621579359044262E-5,2.333370637143297E-5,2.413523293164272E-5,2.5028202640983903E-5,2.601369427509836E-5,2.709179778314753E-5,2.8261606655815497E-5,2.9521227322089023E-5,3.086780598211125E-5,3.229757301419527E-5,3.38059048111979E-5,3.538740260823528E-5,3.703598756401141E-5,3.8745011056194056E-5,4.05073788521382E-5,4.231568752512684E-5,4.416237120881484E-5,4.603985652465865E-5,4.7940723284858945E-5,4.985786837280905E-5,5.178467004013704E-5,5.3715149739731556E-5,5.564412854270669E-5,5.756737516846214E-5,5.948174269433965E-5,6.138529110734412E-5,6.327739301632628E-5,6.515882005895456E-5,6.703180781242547E-5,6.890009734744764E-5,7.076895194738353E-5,7.264514794293517E-5,7.45369390803979E-5,7.645399433994152E-5,7.840730964011254E-5,8.040909439521134E-5,8.247263442199563E-5,8.461213320927949E-5,8.68425340560435E-5,8.917932603820455E-5,9.163833716897603E-5,9.423551846113554E-5,9.698672287076071E-5,9.99074832916003E-5,1.0301279386934995E-4,1.0631689890973967E-4,1.0983309355980657E-4,1.1357354024681136E-4,1.1754910456540577E-4,1.2176921391523796E-4,1.2624174171533322E-4,1.3097291946840376E-4,1.3596727833044644E-4,1.412276211738398E-4,1.4675502543294138E-4,1.5254887630896638E-4,1.586069292057528E-4,1.6492539959053892E-4,1.7149907784443303E-4,1.7832146610539295E-4,1.8538493362998024E-4,1.926808868244742E-4,2.0019994983344714E-4,2.0793215143355434E-4,2.158671139668049E-4,2.2399424016141336E-4,2.323028939254076E-4,2.4078257154987098E-4,2.4942306021225497E-4,2.5821458120881447E-4,2.6714791594891336E-4,2.7621451339015666E-4,2.8540657825765686E-4,2.9471714004828124E-4,3.0414010344661586E-4,3.1367028135015986E-4,3.233034121957169E-4,3.3303616367905023E-4,3.428661252516154E-4,3.527917919520535E-4,3.6281254218178537E-4,3.7292861196417976E-4,3.831410680414861E-4,3.9345178187387875E-4,4.0386340622590086E-4,4.143793555766351E-4,4.2500379109290204E-4,4.357416103837511E-4,4.465984417342284E-4,4.5758064202121014E-4,4.686952970670941E-4,4.799502228088617E-4,4.913539653675687E-4,5.029157979098003E-4,5.146457121064296E-4,5.265544020182202E-4,5.386532383710128E-4,5.509542314183592E-4,5.634699809154388E-4,5.762136121295685E-4,5.891986972713022E-4,6.02439162225268E-4,6.159491789697411E-4,6.297430445765536E-4,6.438350481571306E-4,6.582393275470657E-4,6.729697178843828E-4,6.88039594522338E-4,7.034617129174748E-4,7.192480482430112E-4,7.354096374960347E-4,7.519564267986039E-4,7.688971264453472E-4,7.862390760345199E-4,8.039881217497751E-4,8.221485075511734E-4,8.40722781702813E-4,8.597117197271383E-4,8.791142645477757E-4,8.989274842773233E-4,9.191465478352465E-4,9.397647183518781E-4,9.607733641330103E-4,9.821619868268816E-4,0.001003918266350207,0.0010260281220874164,0.0010484757898701314,0.0010712439142628665,0.0010943136557152698,0.0011176648121798915,0.0011412759548260242,0.0011651245774952784

These two plots are identical.
Indeed, `densityPlot` just uses `statDensity` and `area` and performs coordinate mappings under the hood.
And we can customize `densityPlot` layer: `densityPlot()` optionally opens a new context,
where we can configure bars (as in the usual context opened by `area { ... }`) —
even change coordinate mappings from default ones.
`StatDensity` dataset of `densityPlot` is also can be accessed here.

In [9]:
df.plot {
    densityPlot(depth) {
        // Change a column mapped on `y` to `Stat.scaled`
        y(Stat.scaled)
        alpha = 0.7
        fillColor = Color.RED
        borderLine.color = Color.BLACK
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="Z9KyoY"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"scaled"
},
"stat":"identity",
"data":{
"scaled":[0.004691501125621424,0.004733122587657539,0.004767122573980565,0.004794414532972784,0.004816087375972669,0.004833396507532082,0.0048477517757820245,0.004860702463131318,0.004873919495441008,0.004889175102961636,0.004908320217663781,0.004933259938232496,0.004965927435168538,0.005008256703516021,0.005062154599231765,0.005129472616767657,0.005211978879817042,0.005311330824246464,0.005429049051951649,0.005566492826771649,0.0057248376687588365,0.005905055481174026,0.006107897615738115,0.006333881246145122,0.006583279377888275,0.006856114774380313,0.007152158025525835,0.007470929925762178,0.007811708264643278,0.008173539064911943,0.008555252231416167,0.008955481500020214,0.009372688499813663,0.009805190665535764,0.010251192661430661,0.01070882090407278,0.011176160701478775,0.011651295460555046,0.01213234735615293,0.012617518804254529,0.013105134040585782,0.013593680075661552,0.014081846279189434,0.014568561842001638,0.015053030373134968,0.015534760913965539,0.016013594690765517,0.01648972698169478,0.01696372354373886,0.017436531128765708,0.017909481714634887,0.01838429018573371,0.01886304531565972,0.01934819403090801,0.019842519065950765,0.020349110254339876,0.020871329834539227,0.021412772280060145,0.02197721928799556,0.02256859067507693,0.02319089203281611,0.023848160080195215,0.024544406721010794,0.025283562860962505,0.026069423064909267,0.02690559213588956,0.027795434673578836,0.028742028620530113,0.02974812373017874,0.030816105792295087,0.031947967331145584,0.033145285351628674,0.03440920655230692,0.035740440255421654,0.037139259127027605,0.0386055075801436,0.040138617575356667,0.041737631361867505,0.04340123054267128,0.04512777070537775,0.04691532073957308,0.04876170586655323,0.05066455334083135,0.052621339747304485,0.05462943881455113,0.05668616869353943,0.05878883771102215,0.06093478769590024,0.06312143409161809,0.0653463022039617,0.06760705908640736,0.06990154072870483,0.07222777438250587,0.07458399602425268,0.07696866311393377,0.07938046295276194,0.0818183170679601,0.08428138215409336,0.08676904817421914,0.08928093426812687,0.09181688312801303,0.09437695448425504,0.09696141829705836,0.09957074817640096,0.10220561545677026,0.10486688423956965,0.10755560759028947,0.11027302494567853,0.11302056065448506,0.11579982345001708,0.11861260653965125,0.1214608879006869,0.12434683029793217,0.1272727804894331,0.1302412670649438,0.1332549963678596,0.13631684598504484,0.13942985534848856,0.14259721307521528,0.1458222407734804,0.14910837315935724,0.15245913445313222,0.15587811115395217,0.15936892141836043,0.16293518138836188,0.1665804689226232,0.17030828527620948,0.1741220153465647,0.1780248871540205,0.18201993125279411,0.1861099407730943,0.1902974327776475,0.19458461157862858,0.1989733346064096,0.20346508135328698,0.2080609258372165,0.21276151294678305,0.2175670389432658,0.22247723631260008,0.22749136308274362,0.23260819665330287,0.23782603212628517,0.2431426850809053,0.24855549870179822,0.2540613551484386,0.2596566910428174,0.26533751695061997,0.271099440735946,0.27693769467830137,0.28284716625037803,0.28882243246312267,0.29485779768842363,0.3009473348670882,0.30708492999917636,0.31326432979420726,0.31947919233002586,0.32572314053162255,0.3319898182360909,0.33827294855879814,0.34456639422087965,0.35086421944167406,0.35716075294424837,0.3634506515699877,0.36972896395159,0.3759911936542

If we specify weights, `Stat.densityWeighted` is mapped to `y` by default:

In [10]:
df.plot {
    densityPlot(depth, coeff, n = 700, adjust = 0.8, bandWidth = BandWidth.value(17.0))
    // We can add other layers as well.
    // Let's add a horizontal mark line with constant y intercept:
    vLine {
        // Count sample mean
        val mean = depth.mean()
        xIntercept.constant(mean)
        tooltips { line("Depth mean: ${String.format("%.2f", mean)}m") }
        color = Color.RED; width = 2.0
    }
    x.axis.name = "depth, m"
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="IMt2g9"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"x",
"name":"depth, m",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[138.65869904057837,139.62131100839738,140.58392297621643,141.54653494403544,142.5091469118545,143.4717588796735,144.43437084749254,145.39698281531156,146.3595947831306,147.32220675094962,148.28481871876866,149.24743068658768,150.21004265440672,151.17265462222574,152.13526659004478,153.0978785578638,154.06049052568284,155.02310249350185,155.9857144613209,156.9483264291399,157.91093839695895,158.87355036477797,159.836162332597,160.79877430041603,161.76138626823507,162.7239982360541,163.68661020387313,164.64922217169214,165.6118341395112,166.5744461073302,167.53705807514925,168.49967004296826,169.4622820107873,170.42489397860632,171.38750594642536,172.35011791424438,173.31272988206342,174.27534184988244,175.23795381770148,176.2005657855205,177.16317775333954,178.12578972115855,179.0884016889776,180.0510136567966,181.01362562461566,181.97623759243467,182.93884956025371,183.90146152807273,184.86407349589177,185.8266854637108,186.7892974315298,187.75190939934885,188.7145213671679,189.6771333349869,190.63974530280592,191.60235727062496,192.564969238444,193.52758120626302,194.49019317408204,195.45280514190108,196.41541710972012,197.37802907753914,198.34064104535815,199.3032530131772,200.26586498099624,201.22847694881526,202.19108891663427,203.15370088445331,204.11631285227236,205.07892482009137,206.0415367879104,207.00414875572943,207.96676072354848,208.9293726913675,209.8919846591865,210.85459662700555,211.8172085948246,212.7798205626436,213.74243253046262,214.70504449828167,215.6676564661007,216.63026843391972,217.59288040173874,218.55549236955778,219.51810433737683,220.48071630519584,221.44332827301486,222.4059402408339,223.36855220865294,224.33116417647196,225.29377614429097,226.25638811211002,227.21900007992906,228.18161204774808,229.1442240155671,230.10683598338613,231.06944795120515,232.03205991902416,232.9946718868432,233.95728385466225,234.91989582248127,235.88250779030028,236.84511975811932,237.80773172593837,238.77034369375738,239.7329556615764,240.69556762939544,241.65817959721448,242.6207915650335,243.58340353285251,244.54601550067156,245.5086274684906,246.47123943630962,247.43385140412863,248.39646337194768,249.35907533976672,250.32168730758573,251.28429927540475,252.2469112432238,253.20952321104284,254.17213517886185,255.13474714668087,256.0973591144999,257.05997108231895,258.022583050138,258.985195017957,259.947806985776,260.91041895359507,261.87303092141406,262.8356428892331,263.79825485705214,264.7608668248712,265.72347879269023,266.6860907605092,267.64870272832826,268.61131469614725,269.5739266639663,270.53653863178533,271.4991505996044,272.4617625674234,273.42437453524246,274.38698650306145,275.3495984708805,276.3122104386995,277.2748224065185,278.23743437433757,279.2000463421566,280.16265830997565,281.1252702777947,282.0878822456137,283.0504942134327,284.0131061812517,284.97571814907076,285.9383301168898,286.90094208470884,287.8635540525279,288.82616602034693,289.7887779881659,290.75138995598496,291.71400192380395,292.676613891623,293.63922585944204,294.6018378272611,295.5644497950801,296.52706176289917,297.48967373071815,298.4522856985372,299.4148976663562,300.3775096341752,301.34012160199427,302.3027335698133,303.26534553763236,304.2279575054514,305.1905694732704,306.15318144108943,307.1157934089

### `densityPlot` plot

`densityPlot(statDensityArgs)` and `DataFrame.densityPlot(statDensityArgs)`
are a family of functions for fast plotting a density plot.

In [11]:
densityPlot(depthList, kernel = Kernel.COSINE)

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="Q4qmKq"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.3498068556752156E-5,4.3146918606572777E-5,4.2104807768694464E-5,4.040538693208255E-5,3.810353223831391E-5,3.5273573071460605E-5,3.200689188167934E-5,2.8408973346805624E-5,2.459599815772432E-5,2.06910914178809E-5,1.682034680018044E-5,1.3108754845560648E-5,9.676166882891504E-6,6.6334248996056045E-6,4.0787823337327945E-6,2.0947313638452775E-6,7.453391471613402E-7,7.417902156772859E-8,0.0,0.0,0.0,0.0,0.0,0.0,0.0,0.0,0.0,2.1378932277567928E-7,1.105914109905451E-6,2.664627631589994E-6,4.839597338027073E-6,7.5605910989729696E-6,1.074306905414849E-5,1.4696871294152173E-5,1.958069542427022E-5,2.5236837467578843E-5,3.148265446427637E-5,3.811646221090364E-5,4.492404786196952E-5,5.17127483133002E-5,5.87550862682928E-5,6.600705847783018E-5,7.323449089560872E-5,8.020400189181031E-5,8.66905383989963E-5,9.24846431196902E-5,9.739921812963804E-5,1.012755664726617E-4,1.0398851665745649E-4,1.0545046458077476E-4,1.0561420235891303E-4,1.0458922469108884E-4,1.0293144198016993E-4,1.0075909099569914E-4,9.814231930654821E-5,9.516562530804956E-5,9.19251296771853E-5,8.852547153169925E-5,8.507642951951979E-5,8.168937694718012E-5,7.847368541498297E-5,7.553319308942987E-5,7.270198702306447E-5,6.963679772763277E-5,6.642986042416754E-5,6.318473059563208E-5,6.0006197003038056E-5,5.6985628439361237E-5,5.385106772271245E-5,5.0993087672659325E-5,4.85953852285074E-5,4.691021051914092E-5,4.730948998520499E-5,5.0388953916212276E-5,5.600960879697859E-5,6.347742863038558E-5,7.266125263249191E-5,8.390764177610892E-5,9.769351026844202E-5,1.1394314858336788E-4,1.3213183827944365E-4,1.5167224684352348E-4,1.7193339329448098E-4,1.9226127030056372E-4,2.1236868148031169E-4,2.3193917675684925E-4,2.5029177003116023E-4,2.6684935716011034E-4,2.813252335560366E-4,2.9380641983058807E-4,3.0443301302866295E-4,3.1307910791472063E-4,3.199855069876227E-4,3.249868258687289E-4,3.2792156654820094E-4,3.288937313512696E-4,3.284077228167145E-4,3.271637390885991E-4,3.258445444924666E-4,3.24692085893803E-4,3.247831328844647E-4,3.2634226958506746E-4,3.300035099551671E-4,3.3632483132391215E-4,3.454520786947415E-4,3.581828420319363E-4,3.7448828477403895E-4,3.9296716398805527E-4,4.1280352142088005E-4,4.3363349802216344E-4,4.5520729014048673E-4,4.76931215014341E-4,4.979155652117327E-4,5.171638647094348E-4,5.343074988561315E-4,5.496164227878427E-4,5.632913526008159E-4,5.751190033269402E-4,5.852254842333147E-4,5.933770320329787E-4,5.99455515379703E-4,6.036294876433194E-4,6.062055111976124E-4,6.073807362184766E-4,6.078045773324631E-4,6.080468446288941E-4,6.086165507056388E-4,6.100128353502268E-4,6.131745810864576E-4,6.189567209982205E-4,6.284634122674798E-4,6.419445261067896E-4,6.591704127810308E-4,6.790161313421351E-4,7.009268267852937E-4,7.246273926195575E-4,7.502240549214987E-4,7.773801142114342E-4,8.050053310188915E-4,8.329058802055379E-4,8.60522719184391E-4,8.879421791695173E-4,9.148059521189194E-4,9.40594088392525E-4,9.651247979646198E-4,9.88154977310251E-4,0.0010108816011202243,0.0010341730375997078,0.001058310234792865,0.0010827005029765962,0.0011061514531714996,0.0011289148063258014,0.001150993499566339,0.0011728463504192025,0.0011942899806366496,0.0012157325235817682,0.0012386672541749792,0.0012632093185281643,0.0012902659628619645,0.0013207371581811958,0.0013561072646789713,0.0013961304372647277,0.0014392675071809447,0.0014838399764597508,

In [12]:
df.densityPlot("depth")

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="ptFbsl"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[1.8538371071279594E-5,1.8702837430147296E-5,1.8837187683082854E-5,1.8945031302750088E-5,1.9030671100107746E-5,1.909906778065367E-5,1.9155792330540664E-5,1.920696670762824E-5,1.9259193541397925E-5,1.9319475763561464E-5,1.9395127294073153E-5,1.9493676091555456E-5,1.9622761039838407E-5,1.97900242809183E-5,2.0003000717241172E-5,2.0269006491394745E-5,2.059502830811369E-5,2.0987615491441248E-5,2.1452776668774027E-5,2.1995882943466233E-5,2.2621579359044262E-5,2.333370637143297E-5,2.413523293164272E-5,2.5028202640983903E-5,2.601369427509836E-5,2.709179778314753E-5,2.8261606655815497E-5,2.9521227322089023E-5,3.086780598211125E-5,3.229757301419527E-5,3.38059048111979E-5,3.538740260823528E-5,3.703598756401141E-5,3.8745011056194056E-5,4.05073788521382E-5,4.231568752512684E-5,4.416237120881484E-5,4.603985652465865E-5,4.7940723284858945E-5,4.985786837280905E-5,5.178467004013704E-5,5.3715149739731556E-5,5.564412854270669E-5,5.756737516846214E-5,5.948174269433965E-5,6.138529110734412E-5,6.327739301632628E-5,6.515882005895456E-5,6.703180781242547E-5,6.890009734744764E-5,7.076895194738353E-5,7.264514794293517E-5,7.45369390803979E-5,7.645399433994152E-5,7.840730964011254E-5,8.040909439521134E-5,8.247263442199563E-5,8.461213320927949E-5,8.68425340560435E-5,8.917932603820455E-5,9.163833716897603E-5,9.423551846113554E-5,9.698672287076071E-5,9.99074832916003E-5,1.0301279386934995E-4,1.0631689890973967E-4,1.0983309355980657E-4,1.1357354024681136E-4,1.1754910456540577E-4,1.2176921391523796E-4,1.2624174171533322E-4,1.3097291946840376E-4,1.3596727833044644E-4,1.412276211738398E-4,1.4675502543294138E-4,1.5254887630896638E-4,1.586069292057528E-4,1.6492539959053892E-4,1.7149907784443303E-4,1.7832146610539295E-4,1.8538493362998024E-4,1.926808868244742E-4,2.0019994983344714E-4,2.0793215143355434E-4,2.158671139668049E-4,2.2399424016141336E-4,2.323028939254076E-4,2.4078257154987098E-4,2.4942306021225497E-4,2.5821458120881447E-4,2.6714791594891336E-4,2.7621451339015666E-4,2.8540657825765686E-4,2.9471714004828124E-4,3.0414010344661586E-4,3.1367028135015986E-4,3.233034121957169E-4,3.3303616367905023E-4,3.428661252516154E-4,3.527917919520535E-4,3.6281254218178537E-4,3.7292861196417976E-4,3.831410680414861E-4,3.9345178187387875E-4,4.0386340622590086E-4,4.143793555766351E-4,4.2500379109290204E-4,4.357416103837511E-4,4.465984417342284E-4,4.5758064202121014E-4,4.686952970670941E-4,4.799502228088617E-4,4.913539653675687E-4,5.029157979098003E-4,5.146457121064296E-4,5.265544020182202E-4,5.386532383710128E-4,5.509542314183592E-4,5.634699809154388E-4,5.762136121295685E-4,5.891986972713022E-4,6.02439162225268E-4,6.159491789697411E-4,6.297430445765536E-4,6.438350481571306E-4,6.582393275470657E-4,6.729697178843828E-4,6.88039594522338E-4,7.034617129174748E-4,7.192480482430112E-4,7.354096374960347E-4,7.519564267986039E-4,7.688971264453472E-4,7.862390760345199E-4,8.039881217497751E-4,8.221485075511734E-4,8.40722781702813E-4,8.597117197271383E-4,8.791142645477757E-4,8.989274842773233E-4,9.191465478352465E-4,9.397647183518781E-4,9.607733641330103E-4,9.821619868268816E-4,0.001003918266350207,0.0010260281220874164,0.0010484757898701314,0.0010712439142628665,0.0010943136557152698,0.0011176648121798915,0.0011412759548260242,0.0011651245774952784,0.0011891872595340648,0.0012134398415962417,0.0012378576139319348,0.001262415516565015

In case you want to provide input and weights using column selection DSL,
it's a bit different from the usual one — you should assign `x`
input and (optionally) `weight` throw invocation eponymous functions:

In [13]:
df.densityPlot(adjust = 0.5) {
    x(depth)
    weight(coeff)
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="oFxXw4"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[138.65869904057837,139.97546179107837,141.29222454157838,142.60898729207838,143.9257500425784,145.2425127930784,146.5592755435784,147.8760382940784,149.1928010445784,150.50956379507838,151.82632654557838,153.1430892960784,154.4598520465784,155.7766147970784,157.0933775475784,158.4101402980784,159.7269030485784,161.0436657990784,162.36042854957842,163.67719130007842,164.99395405057842,166.31071680107843,167.62747955157843,168.9442423020784,170.2610050525784,171.57776780307842,172.89453055357842,174.21129330407842,175.52805605457843,176.84481880507843,178.16158155557844,179.47834430607844,180.79510705657844,182.11186980707845,183.42863255757845,184.74539530807846,186.06215805857846,187.37892080907847,188.69568355957847,190.01244631007847,191.32920906057848,192.64597181107848,193.9627345615785,195.27949731207846,196.59626006257847,197.91302281307847,199.22978556357847,200.54654831407848,201.86331106457848,203.1800738150785,204.4968365655785,205.8135993160785,207.1303620665785,208.44712481707847,209.76388756757848,211.08065031807848,212.3974130685785,213.7141758190785,215.0309385695785,216.3477013200785,217.6644640705785,218.9812268210785,220.2979895715785,221.61475232207852,222.93151507257852,224.24827782307852,225.56504057357853,226.88180332407853,228.19856607457854,229.51532882507854,230.83209157557854,232.14885432607855,233.46561707657855,234.78237982707856,236.09914257757856,237.41590532807857,238.73266807857854,240.04943082907855,241.36619357957855,242.68295633007855,243.99971908057856,245.31648183107856,246.63324458157857,247.95000733207857,249.26677008257857,250.58353283307855,251.90029558357855,253.21705833407856,254.53382108457856,255.85058383507857,257.16734658557857,258.4841093360786,259.8008720865786,261.1176348370786,262.4343975875786,263.7511603380786,265.0679230885786,266.3846858390786,267.7014485895786,269.0182113400786,270.3349740905786,271.6517368410786,272.9684995915786,274.2852623420786,275.60202509257863,276.9187878430786,278.23555059357864,279.5523133440786,280.86907609457865,282.1858388450786,283.50260159557865,284.8193643460786,286.13612709657866,287.4528898470786,288.76965259757867,290.0864153480786,291.4031780985787,292.7199408490786,294.0367035995787,295.35346635007863,296.67022910057864,297.98699185107864,299.30375460157865,300.62051735207865,301.93728010257865,303.25404285307866,304.57080560357866,305.88756835407867,307.20433110457867,308.5210938550787,309.8378566055787,311.1546193560787,312.4713821065787,313.7881448570787,315.1049076075787,316.4216703580787,317.7384331085787,319.0551958590787,320.37195860957866,321.6887213600787,323.00548411057866,324.3222468610787,325.6390096115787,326.95577236207873,328.2725351125787,329.58929786307874,330.9060606135787,332.22282336407875,333.5395861145787,334.85634886507876,336.1731116155787,337.48987436607877,338.8066371165787,340.1233998670787,341.4401626175787,342.7569253680787,344.07368811857873,345.39045086907873,346.70721361957874,348.02397637007874,349.34073912057875,350.65750187107875,351.97426462157875,353.29102737207876,354.60779012257876,355.92455287307877,357.24131562357877,358.5580783740788,359.8748411245788,361.1916038750787,362.5083666255788,363.82512937607873,365.1418921265788,366.45865487707874,367.7754176275788,369.09218037807875,370.4089431285788,371.72570587907876,373.0424686295788,374.35

`densityPlot` plot can be configured with `.configure {}` extension — it opens context that combines area,
`StatDensity` and plot context.
That means you can configure bars settings, mappings using `StatDensity` dataset and any plot adjustments:

In [14]:
df.densityPlot {
    x(depth)
}.configure {
    // Area + StatDensity + PlotContext
    // Can't add new layer
    // Can add area mapping, including for `Stat.*` columns
    fillColor(Stat.scaled) // doesn't work properly for now
    alpha = 0.6
    // Can configure general plot adjustments
    layout {
        title = "Configured `densityPlot` plot"
        size = 600 to 350
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="7b599A"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"Configured `densityPlot` plot"
},
"mapping":{
},
"data":{
"density":[1.8538371071279594E-5,1.8702837430147296E-5,1.8837187683082854E-5,1.8945031302750088E-5,1.9030671100107746E-5,1.909906778065367E-5,1.9155792330540664E-5,1.920696670762824E-5,1.9259193541397925E-5,1.9319475763561464E-5,1.9395127294073153E-5,1.9493676091555456E-5,1.9622761039838407E-5,1.97900242809183E-5,2.0003000717241172E-5,2.0269006491394745E-5,2.059502830811369E-5,2.0987615491441248E-5,2.1452776668774027E-5,2.1995882943466233E-5,2.2621579359044262E-5,2.333370637143297E-5,2.413523293164272E-5,2.5028202640983903E-5,2.601369427509836E-5,2.709179778314753E-5,2.8261606655815497E-5,2.9521227322089023E-5,3.086780598211125E-5,3.229757301419527E-5,3.38059048111979E-5,3.538740260823528E-5,3.703598756401141E-5,3.8745011056194056E-5,4.05073788521382E-5,4.231568752512684E-5,4.416237120881484E-5,4.603985652465865E-5,4.7940723284858945E-5,4.985786837280905E-5,5.178467004013704E-5,5.3715149739731556E-5,5.564412854270669E-5,5.756737516846214E-5,5.948174269433965E-5,6.138529110734412E-5,6.327739301632628E-5,6.515882005895456E-5,6.703180781242547E-5,6.890009734744764E-5,7.076895194738353E-5,7.264514794293517E-5,7.45369390803979E-5,7.645399433994152E-5,7.840730964011254E-5,8.040909439521134E-5,8.247263442199563E-5,8.461213320927949E-5,8.68425340560435E-5,8.917932603820455E-5,9.163833716897603E-5,9.423551846113554E-5,9.698672287076071E-5,9.99074832916003E-5,1.0301279386934995E-4,1.0631689890973967E-4,1.0983309355980657E-4,1.1357354024681136E-4,1.1754910456540577E-4,1.2176921391523796E-4,1.2624174171533322E-4,1.3097291946840376E-4,1.3596727833044644E-4,1.412276211738398E-4,1.4675502543294138E-4,1.5254887630896638E-4,1.586069292057528E-4,1.6492539959053892E-4,1.7149907784443303E-4,1.7832146610539295E-4,1.8538493362998024E-4,1.926808868244742E-4,2.0019994983344714E-4,2.0793215143355434E-4,2.158671139668049E-4,2.2399424016141336E-4,2.323028939254076E-4,2.4078257154987098E-4,2.4942306021225497E-4,2.5821458120881447E-4,2.6714791594891336E-4,2.7621451339015666E-4,2.8540657825765686E-4,2.9471714004828124E-4,3.0414010344661586E-4,3.1367028135015986E-4,3.233034121957169E-4,3.3303616367905023E-4,3.428661252516154E-4,3.527917919520535E-4,3.6281254218178537E-4,3.7292861196417976E-4,3.831410680414861E-4,3.9345178187387875E-4,4.0386340622590086E-4,4.143793555766351E-4,4.2500379109290204E-4,4.357416103837511E-4,4.465984417342284E-4,4.5758064202121014E-4,4.686952970670941E-4,4.799502228088617E-4,4.913539653675687E-4,5.029157979098003E-4,5.146457121064296E-4,5.265544020182202E-4,5.386532383710128E-4,5.509542314183592E-4,5.634699809154388E-4,5.762136121295685E-4,5.891986972713022E-4,6.02439162225268E-4,6.159491789697411E-4,6.297430445765536E-4,6.438350481571306E-4,6.582393275470657E-4,6.729697178843828E-4,6.88039594522338E-4,7.034617129174748E-4,7.192480482430112E-4,7.354096374960347E-4,7.519564267986039E-4,7.688971264453472E-4,7.862390760345199E-4,8.039881217497751E-4,8.221485075511734E-4,8.40722781702813E-4,8.597117197271383E-4,8.791142645477757E-4,8.989274842773233E-4,9.191465478352465E-4,9.397647183518781E-4,9.607733641330103E-4,9.821619868268816E-4,0.001003918266350207,0.0010260281220874164,0.0010484757898701314,0.0010712439142628665,0.0010943136557152698,0.0011176648121798915,0.0011412759548260242,0.0011651245774952784,0.0011891872595340648,0.0012134398415962417,0.0012378576139319348,0.0012624155165650154,0.0012870883506135666,0.001311850999829421,0.0013366786612308934,0.0013615470834856462,0.0013864328114773848,0.0014113134352709057,0.0014361678414838515,0.0014609764648892516,0.00148572153791680

## Grouped `statDensity`

`statDensity` can be applied for grouped data —
statistics will be calculated on each group independently but with equal categories.
This application returns a new `GroupBy`
dataset with the same keys as the old one but with `StatDensity` groups instead of old ones.

In [15]:
// Create two samples from normal distribution with different mean/std
val rangesA = NormalDistribution(500.0, 100.0).sample(5000).toList()
val rangesB = NormalDistribution(400.0, 80.0).sample(5000).toList()

// Gather them into `DataFrame` with "A" and "B" keys in the "category" column
val rangesDF = dataFrameOf(
    "range" to rangesA + rangesB,
    "category" to List(5000) { "A" } + List(5000) { "B" }
)
rangesDF.head()

<iframe onload="o_resize_iframe_out_3()" style="width:100%;" class="result_container" id="iframe_out_3" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_838860804"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let

It has the following signature:

| range | category |
|-------|----------|

In [16]:
// Group it by "category"
val groupedRangesDF = rangesDF.groupBy { category }
groupedRangesDF

<iframe onload="o_resize_iframe_out_4()" style="width:100%;" class="result_container" id="iframe_out_4" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_838860806"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++) {


Now we have a `GroupBy` with a signature

<table>
  <thead>
    <tr>
      <th>key: [category]</th>
      <th>group: DataFrame[range|category]</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>A</td>
      <td>A-Group</td>
    </tr>
    <tr>
      <td>B</td>
      <td>B-Group</td>
    </tr>
  </tbody>
</table>

In [17]:
groupedRangesDF.statDensity { x(range) }

<iframe onload="o_resize_iframe_out_5()" style="width:100%;" class="result_container" id="iframe_out_5" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}


:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 <table class="dataframe" id="df_838860812"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++) {


After `statDensity` applying it's still a `GroupBy` but with different signature of `group` -
all groups have the same signature as usual `DataFrame` after `statDensity` applying (i.e. `StatDensityFrame`):

<table>
  <thead>
    <tr>
      <th>key: [drv]</th>
      <th>group: StaDensityFrame</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>"A"</td>
      <td>"A"-Group</td>
    </tr>
    <tr>
      <td>"B"</td>
      <td>"B"-Group</td>
    </tr>
  </tbody>
</table>

As you can see, we did indeed do a `statDensity` transformation within groups, the grouping keys did not change.
The plotting process doesn't change much — we do everything the same.

In [18]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="drth8s"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

As you can see, there are two lines because we have two groups of data.
To distinguish them, we need to add mapping to the color from the key.
This is convenient — the key is available in the context

In [19]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
            color(key.category)
        }
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="0XgzUG"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","

The `densityPlot()` layer also works.
Moreover, if we have exactly one grouping key, a mapping from it to `fillColor`
and `borderLine.color` will be created by default.

In [20]:
groupedRangesDF.plot {
    densityPlot(range)
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="L5yCwm"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

We can customize it like we used to. From the differences — access to `key` columns:

In [21]:
groupedRangesDF.plot {
    densityPlot(range) {
        // Customize scale of default mapping
        fillColor(key.category) {
            scale = categorical("A" to Color.GREEN, "B" to Color.ORANGE)
        }
        borderLine.color = Color.BLACK
        alpha = 0.5
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="amCEtz"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"values":["#3ba272","#fc8452"],
"limits":["A","B"]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","

Also, we can stack areas (for that we need `x` coordinates to match — use `trim = true`):

In [22]:
groupedRangesDF.plot {
    // Use trim
    densityPlot(range, trim = true) {
        // Adjust position of areas from different groups
        position = Position.stack()
        alpha = 0.8
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="bwFIcs"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

`densityPlot` plot for `GroupBy` (i.e. `GroupBy.densityPlot(statDensityArgs)` extensions) works as well:

In [23]:
groupedRangesDF.densityPlot("range", bandWidth = BandWidth.value(10.0))

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="mzCJ9D"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

... and can be configured the same way:

In [24]:
groupedRangesDF.densityPlot(n = 750, trim = true, adjust = 0.75) { x(range) }.configure {
    alpha = 0.6
    position = Position.stack()
    // Can access key column by name as `String`
    fillColor("category") { scale = categoricalColorBrewer(BrewerPalette.Qualitative.Dark2) }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="W9A9D4"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

### Inside `groupBy{}` plot context

We can apply `groupBy` modification to the initial dataset and build a density plot with grouped data the same way:

In [25]:
rangesDF.plot {
    groupBy(category) {
        densityPlot(range)
    }
}

<head>
 <meta charset="UTF-8">
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.2.0/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="x4Hrdm"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",